In [1]:
import pandas as pd
import numpy as np

# 1. Priprava

In [10]:
podatki = pd.read_csv('DN4_1_podatki.csv')
podatki["deltaT"] = podatki["Tw"] - podatki["Ta"]
podatki = podatki.drop(["Tw", "Ta"], axis=1)
podatki.to_csv('podatki_delta.csv', index=False)
podatki_sin = pd.read_csv('podatki_delta.csv')
podatki_sin["sintheta"] = np.sin(podatki["theta"])
podatki_sin = podatki.drop(["theta"], axis=1)

In [ ]:
def izracun_napake(enacba):
    podatki["razlika^2"] = (podatki["Q"] - enacba(podatki["theta"], podatki["eta"], podatki["deltaT"])) ** 2
    return sum(podatki["razlika^2"])/ 500

# 2. Linearna regresija

In [5]:
def linearna_regresija(X, y, meja=1e-2):
    imena = X.columns
    beta = np.linalg.pinv(X.T.dot(X)).dot(X.T).dot(y)

    izraz = ""
    for i,b in enumerate(beta):
        if b > meja:
            if len(izraz) > 0:
                izraz += " + "
            izraz +=  f"{b:.3f}*{imena[i]}"
    return izraz

In [6]:
def ridge_regresija(X, y, lam=1, meja=1e-2):
    imena = X.columns
    beta = np.linalg.pinv(X.T.dot(X) + lam*np.identity(X.shape[1])).dot(X.T).dot(y)

    izraz = ""
    for i,b in enumerate(beta):
        if b > meja:
            if len(izraz) > 0:
                izraz += " + "
            izraz +=  f"{b:.3f}*{imena[i]}"
    return izraz


In [7]:
from scipy.optimize import minimize
def lasso_regresija(X, y, lam=1, meja=1e-2):
    imena = X.columns

    def f(beta):
        yhat = X.dot(beta)
        return np.sum((yhat-y)**2) + lam*np.sum(np.abs(beta))
    beta = minimize(f, np.random.random(X.shape[1]))["x"]
    
    izraz = ""
    for i,b in enumerate(beta):
        if b > meja:
            if len(izraz) > 0:
                izraz += " + "
            izraz +=  f"{b:.3f}*{imena[i]}"
    return izraz

In [11]:
from sklearn.preprocessing import PolynomialFeatures

poly = PolynomialFeatures(3)
X = poly.fit_transform(podatki_sin.drop("Q", axis=1))

imena_stolpcev = poly.get_feature_names_out()
X_df = pd.DataFrame(X, columns=imena_stolpcev)

In [ ]:
print(linearna_regresija(X_df, podatki["Q"]))
print(ridge_regresija(X_df, podatki["Q"], lam= 3))
print(lasso_regresija(X_df, podatki["Q"], lam= 3))

0.096*1 + 0.021*eta + 0.049*eta deltaT + 0.237*eta sin(theta) + 0.048*deltaT sin(theta) + 0.187*eta^3 + 0.025*eta^2 deltaT + 0.267*eta^2 sin(theta) + 0.165*eta sin(theta)^2 + 0.016*sin(theta)^3
0.023*1 + 0.038*eta deltaT + 0.096*eta sin(theta) + 0.038*deltaT sin(theta) + 0.023*eta^2 deltaT + 0.097*eta^2 sin(theta) + 0.127*eta sin(theta)^2
0.032*eta deltaT + 0.033*deltaT sin(theta) + 0.021*eta^2 deltaT


In [14]:
podatki["1-eta"] = 1 - podatki["eta"]
podatki = podatki.drop(["theta", "eta"], axis=1)

In [15]:
poly = PolynomialFeatures(3)
X = poly.fit_transform(podatki.drop("Q", axis=1))

imena_stolpcev = poly.get_feature_names_out()
X_df = pd.DataFrame(X, columns=imena_stolpcev)

In [ ]:
print(linearna_regresija(X_df, podatki["Q"]))
print(ridge_regresija(X_df, podatki["Q"], lam= 3))
print(lasso_regresija(X_df, podatki["Q"], lam= 3))

0.048*deltaT + 0.394*sin(theta) + 0.602*1-eta + 0.020*sin(theta)^2 + 0.117*deltaT sin(theta) 1-eta + 0.025*deltaT 1-eta^2 + 0.016*sin(theta)^3 + 0.267*sin(theta) 1-eta^2
0.035*deltaT + 0.041*sin(theta) + 0.068*1-eta + 0.043*sin(theta)^2 + 0.039*1-eta^2 + 0.100*deltaT sin(theta) 1-eta + 0.020*deltaT 1-eta^2 + 0.041*sin(theta)^3
0.033*deltaT + 0.085*deltaT sin(theta) 1-eta + 0.016*deltaT 1-eta^2


# 3. ProGED

In [ ]:
import ProGED as pg

In [ ]:
np.random.seed(15)
gramatika1 = "E -> E '*' F [0.6] | F [0.4] \n"
gramatika1 += "F -> F '+' K [0.1] | F '-' K [0.1] | K [0.8] \n"
gramatika1 += "K -> T '(' M ')' [0.3] |  | 'C' [0.2] | V [0.5] \n"
gramatika1 += "T -> 'sin' [1]  \n"
gramatika1 += "M -> 'theta' [1] \n"
gramatika1 += "V -> 'deltaT' [0.6] | 'eta' [0.4]"
gramatika1 = pg.GeneratorGrammar(gramatika1)

In [ ]:

ED = pg.EqDisco(data=podatki, 
                sample_size=100,
                lhs_vars=["Q"],
                rhs_vars=["deltaT", "theta", "eta"],
                generator = gramatika1)
ED.generate_models()

ModelBox: 62 models
-> [deltaT], p = 0.096
-> [eta], p = 0.06400000000000002
-> [deltaT*eta - eta*sin(theta)], p = 2.654208000000001e-05
-> [C0*deltaT], p = 0.018432000000000004
-> [deltaT*sin(theta)], p = 0.027648
-> [sin(theta)], p = 0.096
-> [deltaT**2], p = 0.013824
-> [eta**2*sin(theta)**4], p = 2.6418075402240005e-06
-> [eta**2], p = 0.006144000000000003
-> [C0*deltaT + deltaT], p = 2.6542080000000007e-05
-> [C0 + deltaT*eta*sin(theta)], p = 2.6542080000000003e-05
-> [C0*deltaT**2 + eta - sin(theta)], p = 7.962624000000001e-07
-> [deltaT*eta**2*sin(theta)], p = 0.00012740198400000005
-> [C0 - deltaT**2*eta - eta**2], p = 4.892236185600005e-09
-> [-deltaT + 2*sin(theta)], p = 8.640000000000001e-05
-> [C0*deltaT**3*eta*sin(theta)**2], p = 3.80420285792256e-07
-> [deltaT*sin(theta)**2], p = 0.0019906559999999995
-> [C0*deltaT*sin(theta)**2], p = 0.00038220595200000004
-> [deltaT*eta*sin(theta)**2], p = 0.000191102976
-> [C0*deltaT + eta*sin(theta) + eta], p = 5.308416000000002e-07
-

In [ ]:
ED.fit_models()
ED.get_results(20)

ModelBox: 20 models
-> [0.00326687307136254*deltaT**2*sin(theta)], p = 0.000191102976, error = 0.3537096351617019, time = 0.10193729400634766
-> [0.0876061255382262*deltaT*sin(theta)], p = 0.0013271040000000002, error = 0.5620851399146056, time = 0.10294198989868164
-> [0.0993586357156735*deltaT*sin(theta)**2], p = 0.00038220595200000004, error = 0.5876480490887231, time = 0.07597541809082031
-> [0.000111889895057901*deltaT**3*sin(theta)**4], p = 8.21707817311273e-08, error = 0.6136238671167338, time = 0.3328213691711426
-> [0.00209573507837829*deltaT**2 - 0.00587808818293187], p = 2.654208000000001e-05, error = 0.6555954301067569, time = 0.5686149597167969
-> [0.00208863392795897*deltaT**2], p = 0.0013271040000000002, error = 0.6556113356599887, time = 0.2618546485900879
-> [0.00290912989093892*deltaT**2*sin(theta)**2 + eta], p = 5.503765708800002e-07, error = 0.6910658173168978, time = 0.2898440361022949
-> [5.94389524024101e-5*deltaT**3], p = 0.00019110297600000002, error = 0.698682

In [ ]:

ED = pg.EqDisco(data=podatki, 
                sample_size=1000,
                lhs_vars=["Q"],
                rhs_vars=["deltaT", "theta", "eta"],
                generator = gramatika1)
ED.generate_models()

ModelBox: 357 models
-> [deltaT], p = 0.0960864
-> [eta], p = 0.06400000000000002
-> [deltaT*eta - eta*sin(theta)], p = 2.654208000000001e-05
-> [C0*deltaT], p = 0.019343278080000005
-> [deltaT*sin(theta)], p = 0.027648
-> [sin(theta)], p = 0.096
-> [deltaT**2], p = 0.013824
-> [eta**2*sin(theta)**4], p = 2.6418075402240005e-06
-> [eta**2], p = 0.006144000000000003
-> [C0*deltaT + deltaT], p = 2.7338342400000007e-05
-> [C0 + deltaT*eta*sin(theta)], p = 2.6542080000000003e-05
-> [C0*deltaT**2 + eta - sin(theta)], p = 7.962624000000001e-07
-> [deltaT*eta**2*sin(theta)], p = 0.0002548039680000001
-> [C0 - deltaT**2*eta - eta**2], p = 4.892236185600005e-09
-> [-deltaT + 2*sin(theta)], p = 0.00017280000000000003
-> [C0*deltaT**3*eta*sin(theta)**2], p = 3.80420285792256e-07
-> [deltaT*sin(theta)**2], p = 0.0059719679999999985
-> [C0*deltaT*sin(theta)**2], p = 0.0005916548136960001
-> [deltaT*eta*sin(theta)**2], p = 0.000764411904
-> [C0*deltaT + eta*sin(theta) + eta], p = 5.308416000000002e-

In [ ]:
ED.fit_models()
ED.get_results(20)

ModelBox: 20 models
-> [-0.00308074032382619*deltaT**2*eta**2*sin(theta) + 0.0042040853181083*deltaT**2*sin(theta)], p = 9.693259832756094e-13, error = 0.15346360192655512, time = 0.734001874923706
-> [0.00326687307230029*deltaT**2*sin(theta)], p = 0.000402313042722816, error = 0.3537096351616991, time = 0.11193585395812988
-> [0.00368373675350053*deltaT**2*sin(theta)**2 - 0.275377417980387*sin(theta) + 0.234305052639025], p = 1.2562464743251897e-16, error = 0.389032032061854, time = 0.5697031021118164
-> [0.00368182039949037*deltaT**2*sin(theta)**2], p = 5.77042315739136e-05, error = 0.40240334730703137, time = 0.3567969799041748
-> [0.00376985660423874*deltaT**2*sin(theta)**3 + eta*sin(theta)**2 - 1.76565055151758*eta*sin(theta) + 0.45407308028128], p = 9.087431093208838e-15, error = 0.42651475135009675, time = 1.1681005954742432
-> [0.00371508488335292*deltaT**2*sin(theta)**3 + 0.134214860494572*sin(theta)], p = 3.2868312692450934e-11, error = 0.4747953225845042, time = 0.2099251747

In [ ]:

ED = pg.EqDisco(data=podatki, 
                sample_size=1000000,
                lhs_vars=["Q"],
                rhs_vars=["deltaT", "theta", "eta"],
                generator = gramatika1)
ED.generate_models()

ModelBox: 64927 models
-> [deltaT**2 + deltaT + eta - sin(theta)], p = 9.953280000000002e-07
-> [C0*eta*sin(theta) + deltaT + 2*sin(theta)], p = 5.236221542400002e-08
-> [sin(theta)], p = 0.0967247400429456
-> [eta**2], p = 0.006198418419701518
-> [sin(theta)**2], p = 0.013947364756684798
-> [C0 + sin(theta)], p = 0.006811276307499017
-> [eta*sin(theta)], p = 0.018595812016523137
-> [eta*sin(theta)**2], p = 0.0040060461818587694
-> [C0*deltaT + eta], p = 0.001288878140187259
-> [deltaT*sin(theta)], p = 0.027893315041588398
-> [C0*deltaT**2], p = 0.004922295709080033
-> [eta], p = 0.0645390586950206
-> [eta*sin(theta)**2 + eta], p = 0.00015928699497534776
-> [C0*sin(theta)**2], p = 0.004919312399540728
-> [sin(theta)**2 - sin(theta)], p = 0.000415847819593728
-> [deltaT**2*sin(theta)**2], p = 0.001722970670978669
-> [C0*deltaT*sin(theta) + sin(theta)], p = 0.0008580525096374348
-> [deltaT**2*sin(theta) + eta], p = 0.00023887946300837069
-> [C0*deltaT], p = 0.021997268207763203
-> [C0 - 

In [ ]:
ED.fit_models()
ED.get_results(20)

Model skipped. More model parameters than allowed (check max constant).
Model skipped. More model parameters than allowed (check max constant).
Model skipped. More model parameters than allowed (check max constant).
Model skipped. More model parameters than allowed (check max constant).
Model skipped. More model parameters than allowed (check max constant).
Model skipped. More model parameters than allowed (check max constant).
Model skipped. More model parameters than allowed (check max constant).


ModelBox: 20 models
-> [-0.00317370298069512*deltaT**2*eta*sin(theta) + 0.00479802435721139*deltaT**2*sin(theta) - 2.08226317207104e-5*deltaT**2], p = 4.3619669247402416e-14, error = 0.11535069324568051, time = 0.7679109573364258
-> [-0.0031338912196254*deltaT**2*eta*sin(theta) - 3.22532069322885e-5*deltaT**2*eta + 0.00477243972351006*deltaT**2*sin(theta)], p = 4.361966924740239e-14, error = 0.11537549785679053, time = 1.277031421661377
-> [-0.00317104041865663*deltaT**2*eta*sin(theta) + 0.0047726220588923*deltaT**2*sin(theta) - 0.00260893686118057*eta], p = 2.0194291318241851e-13, error = 0.11544222916942984, time = 1.2113080024719238
-> [-0.00317528248584184*deltaT**2*eta*sin(theta) + 0.00477369635710848*deltaT**2*sin(theta) - 0.000673782828950437], p = 2.10357201231686e-12, error = 0.1154474644044027, time = 0.6136791706085205
-> [-0.00317554234770622*deltaT**2*eta*sin(theta) + 0.00477281658802083*deltaT**2*sin(theta) - 2.14335939356614e-5*sin(theta)], p = 3.029143697736278e-13, err

# 4. pySR

In [ ]:
from pysr import PySRRegressor

In [ ]:
model = PySRRegressor(
    niterations=40,  # < Increase me for better results
    binary_operators=["+", "*", "-", "/"],
    unary_operators=[
        "exp",
        "sin",
        "cos",
        "sinh",
        "log",
        "sqrt",
        "cosh",
        "tan"
        # ^ Custom operator (julia syntax)
    ],
    extra_sympy_mappings={"inv": lambda x: 1 / x},
    # ^ Define operator for SymPy as well
    loss="loss(prediction, target) = (prediction - target)^2",
    # ^ Custom loss function (julia syntax)
)

In [ ]:
X = podatki.drop("Q", axis=1)
y = podatki["Q"]
model.fit(X, y)

c:\Users\HP\AppData\Local\Programs\Python\Python39\lib\site-packages\pysr\sr.py:1296: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
c:\Users\HP\AppData\Local\Programs\Python\Python39\lib\site-packages\pysr\sr.py:1364: FutureWarning: Index.is_object is deprecated.Use pandas.api.types.is_object_dtype instead
  if X.columns.is_object() and X.columns.str.contains(" ").any():


PySRRegressor.equations_ = [
	    pick     score                                           equation  \
	0         0.000000                                          0.6829461   
	1         0.114405                                         sin(theta)   
	2         0.584469                             (0.056376774 * deltaT)   
	3         0.193638                          sinh(0.04553223 * deltaT)   
	4         0.012138                      ((deltaT * 0.07771593) - eta)   
	5         0.379150                (0.0837108 * (deltaT * sin(theta)))   
	6         0.558591          sinh(0.057081196 * (deltaT * sin(theta)))   
	7         0.190881  (0.0036934207 * ((deltaT * sin(theta)) * deltaT))   
	8         0.184988  (tan(0.0032668333) * ((deltaT * sin(theta)) * ...   
	9         0.089279  sinh((eta * -0.36319888) - (-0.06563826 * (del...   
	10        0.593769  sinh((-0.46700364 * eta) - (-0.063772686 * (de...   
	11  >>>>  1.337283  (0.059568606 * (deltaT * (0.08741735 * ((delta...   
	12        0.009069  (0.059568606 * (deltaT * (sin(0.08741735) * ((...   
	13        0.082658  (0.059568606 * ((deltaT - 1.1164955) * (0.0874...   
	14        0.008268  (0.059568606 * ((deltaT + sin(-1.3117963)) * (...   
	15        0.001760  (0.059568606 * ((deltaT + sin(sin(-1.3117963))...   
	16        0.021584  (sqrt(exp(sinh(sin(exp(1.3554826))))) * (delta...   
	17        0.031453  (deltaT * sinh(0.0072383448 * ((deltaT / sinh(...   
	18        0.006421  (deltaT * sinh(0.0072383448 * ((deltaT / sinh(...   
	
	        loss  complexity  
	0   1.149930           1  
	1   1.025619           2  
	2   0.571682           3  
	3   0.471041           4  
	4   0.465358           5  
	5   0.318511           6  
	6   0.182193           7  
	7   0.150533           8  
	8   0.125110           9  
	9   0.104652          11  
	10  0.057793          12  
	11  0.015174          13  
	12  0.015037          14  
	13  0.013844          15  
	14  0.013730          16  
	15  0.013706          17  
	16  0.013413          18  
	17  0.012998          19  
	18  0.012915          20  
]

In [ ]:
model.sympy()

0.0052073296797141*deltaT**2*exp(-eta)*sin(theta)

In [ ]:
model = PySRRegressor(
    niterations=40,  # < Increase me for better results
    binary_operators=["+", "*", "-", "/"],
    unary_operators=[
        "sin"
        # ^ Custom operator (julia syntax)
    ],
    #extra_sympy_mappings={"inv": lambda x: 1 / x},
    # ^ Define operator for SymPy as well
    loss="loss(prediction, target) = (prediction - target)^2",
    # ^ Custom loss function (julia syntax)
)

In [ ]:
X = podatki.drop("Q", axis=1)
y = podatki["Q"]
model.fit(X, y)

c:\Users\HP\AppData\Local\Programs\Python\Python39\lib\site-packages\pysr\sr.py:1296: UserWarning: Note: it looks like you are running in Jupyter. The progress bar will be turned off.
  warnings.warn(
c:\Users\HP\AppData\Local\Programs\Python\Python39\lib\site-packages\pysr\sr.py:1364: FutureWarning: Index.is_object is deprecated.Use pandas.api.types.is_object_dtype instead
  if X.columns.is_object() and X.columns.str.contains(" ").any():


PySRRegressor.equations_ = [
	    pick     score                                           equation  \
	0         0.000000                                         0.68310344   
	1         0.114405                                         sin(theta)   
	2         0.584469                             (0.056376807 * deltaT)   
	3         0.142601                 ((0.0020886636 * deltaT) * deltaT)   
	4         0.307830               ((0.08760638 * deltaT) * sin(theta))   
	5         0.463177   ((deltaT * (0.003266907 * deltaT)) * sin(theta))   
	6         0.040384  ((0.0032977413 * deltaT) * ((sin(theta) * delt...   
	7         0.001686  (sin(0.0033531212 * deltaT) * ((sin(theta) * d...   
	8   >>>>  2.156844  (((0.0031754542 * (deltaT * (1.5030172 - eta))...   
	9         0.000151  (((0.0031754542 * (deltaT * (1.5030172 - eta))...   
	10        0.036697  ((sin(sin(0.0037746492 * (deltaT * (1.3076622 ...   
	11        0.001292  ((sin(sin(sin(0.0037746492 * (deltaT * (1.3076...   
	12        0.005244  (((0.0031754542 * ((deltaT * (1.5030172 - eta)...   
	13        0.004549  (((0.0031754542 * ((deltaT * (1.5030172 - eta)...   
	
	        loss  complexity  
	0   1.149930           1  
	1   1.025619           2  
	2   0.571682           3  
	3   0.429826           5  
	4   0.315940           6  
	5   0.125110           8  
	6   0.115403          10  
	7   0.115208          11  
	8   0.013328          12  
	9   0.013324          14  
	10  0.012844          15  
	11  0.012828          16  
	12  0.012694          18  
	13  0.012579          20  
]

In [ ]:
model.sympy()

0.0031754542*deltaT**2*(1.5030172 - eta)*sin(theta)